In [ ]:
import pandas as pd
import numpy as np
import datetime

from analytics.basket_index import MarkitBasketIndex
from analytics import on_the_run
import matplotlib.pyplot as plt

from utils.db import dbengine
serenitas_engine = dbengine('serenitasdb')

%matplotlib inline

In [ ]:
value_date = (pd.datetime.today() - pd.offsets.BDay(1)).date()
index_type = 'HY'
series = 32

In [ ]:
sql_string = "select * from index_members(%s, %s)"

df = pd.read_sql_query(sql_string, serenitas_engine, params=(index_type + str(series), value_date), index_col=['markit_ticker'])
df1 = pd.read_sql_query(sql_string, serenitas_engine, params=(index_type + str(series-2), value_date), index_col=['markit_ticker'])

default_prob = {}
for s in [series, series-2]:
    index = MarkitBasketIndex(index_type, s, ['5yr'])
    surv_prob, tickers = index.survival_matrix()
    default_prob[s] = pd.Series(1 - np.ravel(surv_prob), index=tickers)
default_prob = pd.concat(default_prob, names=['series', 'markit_ticker'])
default_prob.name = 'default_prob'

df = df.merge(default_prob.loc[series], left_index=True, right_index = True)
df1 = df1.merge(default_prob.loc[series-2], left_index=True, right_index = True)

In [ ]:
#Removals
df1.loc[df1.index.difference(df.index)]

In [ ]:
#Additions
df.loc[df.index.difference(df1.index)]

In [ ]:
date_range = pd.bdate_range(value_date - 52 * .5 * pd.offsets.Week(), value_date, freq='5B')
index = MarkitBasketIndex(index_type, series, ['5yr'])
default_prob = {}
for d in date_range:
    index.value_date = d
    surv_prob, tickers = index.survival_matrix()
    default_prob[d] = pd.Series(1 - np.ravel(surv_prob), index=tickers)
default_prob = pd.concat(default_prob)

In [ ]:
#Top 20 highest cumulative
top20 = default_prob.unstack(-1)[default_prob[value_date].nlargest(20).index]
top20.index.name='date'
top20.columns.name='tickers'
ax = top20.plot(title=f'market implied default probabilities to {index.maturities[0]}', figsize=(10,6))
ax.legend(loc='upper center', bbox_to_anchor=(1.3, 1), ncol=1)
ax.set(xlabel='date', ylabel='probability')
plt.tight_layout()

In [ ]:
tenors = ['3yr', '5yr', '7yr', '10yr']
#index_type = 'IG'
#series = 26
indices = MarkitBasketIndex(index_type, series, tenors)
indices.value_date = datetime.date.today()
today_surv_prob, tickers = indices.survival_matrix()
today_default_prob = pd.DataFrame(1 - today_surv_prob, index=tickers, columns=tenors)

In [ ]:
#Dispersion: std_dev of default_prob/average default_prob
date_range = pd.bdate_range(value_date - 52 * 4 * pd.offsets.Week(), value_date, freq='5B')
default_prob = {}
ontr = on_the_run(index_type, date_range[0])
index = MarkitBasketIndex(index_type, ontr, ['5yr'])
for d in date_range:
    if ontr != on_the_run(index_type, d):
        ontr = on_the_run(index_type, d)
        index = MarkitBasketIndex(index_type, ontr, ['5yr'])
    try:
        index.value_date = d
        surv_prob, tickers = index.survival_matrix()
        default_prob[d] = pd.Series(1 - np.ravel(surv_prob), index=tickers)
    except:
        continue
default_prob = pd.concat(default_prob)
dispersion = default_prob.unstack(level=0)
dispersion = dispersion.std()/dispersion.mean()
dispersion.plot()

In [ ]:
def gini(array):
    """Calculate the Gini coefficient of a numpy array."""
    array = array.values
    # based on bottom eq: http://www.statsdirect.com/help/content/image/stat0206_wmf.gif
    # from: http://www.statsdirect.com/help/default.htm#nonparametric_methods/gini.htm
    if np.amin(array) < 0:
        array -= np.amin(array) #values cannot be negative
    array += 0.0000001 #values cannot be 0
    array = np.sort(array) #values must be sorted
    index = np.arange(1,array.shape[0]+1) #index per array element
    n = array.shape[0]#number of array elements
    return ((np.sum((2 * index - n  - 1) * array)) / (n * np.sum(array))) #Gini coefficient

In [ ]:
#Instead of std dev of spread get Gini Factor default prob
sql_string = "select * from index_version where index = %s"
idx_ver = pd.read_sql_query(sql_string, serenitas_engine, params=[index_type,], parse_dates=['lastdate'])
idx_ver['date'] = pd.to_datetime([d.strftime('%Y-%m-%d') if not pd.isnull(d) else datetime.date(2050,1,1) for d in idx_ver['lastdate']])
sql_string = "select * from risk_numbers where index = %s"
risk = pd.read_sql_query(sql_string, serenitas_engine, parse_dates={'date': {'utc':True}}, params=[index_type])
risk.date = risk.date.dt.normalize().dt.tz_convert(None)
risk = risk.groupby(['date','index','series','tenor','attach']).mean()
risk.reset_index(inplace=True)
idx_ver.sort_values(by=['date'], inplace=True, ascending=True)
risk = pd.merge_asof(risk, idx_ver[['date','series','cumulativeloss','indexfactor']], left_on=['date'], right_on=['date'], by='series', direction='forward')
risk.set_index('date', inplace=True) 
risk['moneyness'] = risk.apply(lambda df: (df.detach-df.cumulativeloss)/df.indexfactor/df.index_expected_loss, axis=1)

single_day_risk = {}
date_range = pd.bdate_range(value_date - 52 * 5 * pd.offsets.Week(), value_date, freq='5B')
for d in date_range:
    default_prob={}
    try:
        df = risk.loc[d]
    except:
        continue
    for s in df.series.unique():
        tenors = list(df[df.series==s]['tenor'].sort_values().unique())
        indices = MarkitBasketIndex(index_type, s, tenors)
        try:
            indices.value_date = d
            surv_prob, tickers = indices.survival_matrix()
            default_prob[s] = pd.DataFrame(1 - surv_prob, index=tickers, columns=tenors)
        except:
            continue
    if default_prob:
        default_prob = pd.concat(default_prob, names=['series', 'name'], sort=True)
        default_prob.columns.name = 'tenor'
        gini_coeff = default_prob.stack().groupby(['series', 'tenor']).apply(gini)
        single_day_risk[d] = df.merge(gini_coeff.rename('gini_coeff').reset_index(), on=['series', 'tenor'])
tranche_risk = pd.concat(single_day_risk, names=['date', 'idx'], sort=True)

In [ ]:
to_plot_gini = tranche_risk[(tranche_risk.tenor == '5yr') & (tranche_risk.attach ==0)].groupby(['date', 'series']).nth(-1)
to_plot_gini['gini_coeff'].unstack().plot()

In [ ]:
import statsmodels.formula.api as smf
equity = tranche_risk[tranche_risk.attach==0]
#use a subset for modeling purposes?
equity = equity[(equity.tenor=='5yr') & (equity.series >= 27)]
gini_model = smf.gls("corr_at_detach ~ gini_coeff + duration + moneyness", data=equity).fit()
gini_model.summary()

In [ ]:
predict_today = equity.reset_index()[['gini_coeff', 'duration', 'moneyness']].iloc[-1]
spread_gls_model.predict(predict_today)

In [ ]:
#Let's use a GAM model instead?
from pygam import LinearGAM, s, f
X = np.array(equity[['gini_coeff', 'duration', 'moneyness']])
y = np.array(equity['corr_at_detach'])

gam_model = LinearGAM(s(0) + s(1) + s(2))
lam = np.logspace(-3, 5, 5, base=3)
lams = [lam] * 3

gam_model.gridsearch(X, y, lam=lams)
gam_model.summary()

In [ ]:
## plotting
plt.figure();
fig, axs = plt.subplots(1,3);

titles = ['gini_coeff', 'duration', 'moneyness']
for i, ax in enumerate(axs):
    XX = gam_model.generate_X_grid(term=i)
    ax.plot(XX[:, i], gam_model.partial_dependence(term=i, X=XX))
    ax.plot(XX[:, i], gam_model.partial_dependence(term=i, X=XX, width=.95)[1], c='r', ls='--')
    if i == 0:
        ax.set_ylim(-30,30)
    ax.set_title(titles[i]);